<a href="https://colab.research.google.com/github/jotten7137/Meal_Prep/blob/main/MealPrep_Recommendation_System.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Joshua Otten <br>
2023.11.19

# Introduction

The objective of this assignment is to do a recipe and meal-prep recommendation system. I began by assembling multiple data sources that were present on Kaggle from Food.com [Ref. 1, 2] - mainly with the purpose of having a rich dataset that had the criteria of recipe name, recipe servings and relevant labels (col. recommend - concatenation of tags, descriptions and ingredients) to construct a recommendation system.

For the first recommendation method - I used the single factor recommendation methodology. This was beneficial in proof of concept - but limited in the amount of inputs I would want the model to work with and recommend on.

Next Steps:
1. Multi-factor recommendation system with user input



## References
1. Food.com Recipes and Interactions <br>
https://www.kaggle.com/datasets/shuyangli94/food-com-recipes-and-user-interactions/
2. Food.com Recipes with Search Terms and Tags <br>
https://www.kaggle.com/datasets/shuyangli94/foodcom-recipes-with-search-terms-and-tags/data


#1 - Data

**Food.com Recipes and Interactions**<br>
https://www.kaggle.com/datasets/shuyangli94/food-com-recipes-and-user-interactions/

**Citation**<br>
Generating Personalized Recipes from Historical User Preferences
Bodhisattwa Prasad Majumder*, Shuyang Li*, Jianmo Ni, Julian McAuley
EMNLP, 2019
https://www.aclweb.org/anthology/D19-1613/


**Food.com Recipes with Search Terms and Tags** <br>
https://www.kaggle.com/datasets/shuyangli94/foodcom-recipes-with-search-terms-and-tags/data

**Citation**<br>
SHARE: a System for Hierarchical Assistive Recipe Editing
Shuyang Li, Yufei Li, Jianmo Ni, Julian McAuley
arXiv, 2021
https://arxiv.org/pdf/2105.08185.pdf

Generating Personalized Recipes from Historical User Preferences
Bodhisattwa Prasad Majumder*, Shuyang Li*, Jianmo Ni, Julian McAuley
EMNLP, 2019<br>
https://www.aclweb.org/anthology/D19-1613/

In [ ]:
# Install for Kaggle API [Ref. 1]
!pip install opendatasets

In [ ]:
# Dependencies
import opendatasets as od
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Pandas
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [ ]:
import pandas as pd
import numpy as np

from ast import literal_eval
from collections import Counter
from tqdm.auto import tqdm
import warnings

pd.set_option('display.max_colwidth', 1000)
warnings.filterwarnings("ignore")
tqdm.pandas()

In [ ]:
# Kaggle Downloads
# kaggle datasets download -d shuyangli94/foodcom-recipes-with-search-terms-and-tags

# Recipes and Interactions
#kaggle datasets download -d shuyangli94/food-com-recipes-and-user-interactions
od.download("https://www.kaggle.com/datasets/shuyangli94/food-com-recipes-and-user-interactions", force=True)

# Search Terms & Tags
# kaggle datasets download -d shuyangli94/foodcom-recipes-with-search-terms-and-tags
od.download("https://www.kaggle.com/datasets/shuyangli94/foodcom-recipes-with-search-terms-and-tags", force=True)

Please provide your Kaggle credentials to download this dataset. Learn more: http://bit.ly/kaggle-creds
Your Kaggle username: misterotter
Your Kaggle Key: ··········


100%|██████████| 267M/267M [00:05<00:00, 53.9MB/s]



Please provide your Kaggle credentials to download this dataset. Learn more: http://bit.ly/kaggle-creds
Your Kaggle username: misterotter
Your Kaggle Key: ··········


100%|██████████| 231M/231M [00:02<00:00, 108MB/s]


## Food.com Recipes and Interactions

In [ ]:
df_interactions = pd.read_csv("food-com-recipes-and-user-interactions/RAW_interactions.csv")
df_interactions.head()

user_id  recipe_id        date  rating  \
0    38094      40893  2003-02-17       4   
1  1293707      40893  2011-12-21       5   
2     8937      44394  2002-12-01       4   
3   126440      85009  2010-02-27       5   
4    57222      85009  2011-10-01       5   

                                                                                                                                                                                                          review  
0                                                                     Great with a salad. Cooked on top of stove for 15 minutes.Added a shake of cayenne and a pinch of salt.  Used low fat sour cream.  Thanks.  
1  So simple, so delicious! Great for chilly fall evening. Should have doubled it ;)<br/><br/>Second time around, forgot the remaining cumin. We usually love cumin, but didn't notice the missing 1/2 teaspoon!  
2                                                                                                            This worked very well and is EASY.  I used not quite a whole package (10oz) of white chips.  Great!  
3                                                                                                                                           I made the Mexican topping and took it to bunko.  Everyone loved it.  
4                                                                                                                                      Made the cheddar bacon topping, adding a sprinkling of black pepper. Yum!

In [ ]:
df_recipes = pd.read_csv("food-com-recipes-and-user-interactions/RAW_recipes.csv")
df_recipes.head()

name      id  minutes  \
0  arriba   baked winter squash mexican style  137739       55   
1            a bit different  breakfast pizza   31490       30   
2                   all in the kitchen  chili  112140      130   
3                          alouette  potatoes   59389       45   
4          amish  tomato ketchup  for canning   44061      190   

   contributor_id   submitted  \
0           47892  2005-09-16   
1           26278  2002-06-17   
2          196586  2005-02-25   
3           68585  2003-04-14   
4           41706  2002-10-25   

                                                                                                                                                                                                                                                                                                                                                                                                                                     tags  \
0                                                                                                                                                              ['60-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'cuisine', 'preparation', 'occasion', 'north-american', 'side-dishes', 'vegetables', 'mexican', 'easy', 'fall', 'holiday-event', 'vegetarian', 'winter', 'dietary', 'christmas', 'seasonal', 'squash']   
1                                                                                                                                                        ['30-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'cuisine', 'preparation', 'occasion', 'north-american', 'breakfast', 'main-dish', 'pork', 'american', 'oven', 'easy', 'kid-friendly', 'pizza', 'dietary', 'northeastern-united-states', 'meat', 'equipment']   
2                                                                                                                                                                                                                                                                                                     ['time-to-make', 'course', 'preparation', 'main-dish', 'chili', 'crock-pot-slow-cooker', 'dietary', 'equipment', '4-hours-or-less']   
3  ['60-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'side-dishes', 'eggs-dairy', 'potatoes', 'vegetables', 'oven', 'easy', 'dinner-party', 'holiday-event', 'easter', 'cheese', 'stove-top', 'dietary', 'christmas', 'new-years', 'thanksgiving', 'independence-day', 'st-patricks-day', 'valentines-day', 'inexpensive', 'brunch', 'superbowl', 'equipment', 'presentation', 'served-hot']   
4                                                                                       ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'cuisine', 'preparation', 'occasion', 'north-american', 'canning', 'condiments-etc', 'vegetables', 'american', 'heirloom-historical', 'holiday-event', 'vegetarian', 'dietary', 'amish-mennonite', 'northeastern-united-states', 'number-of-servings', 'technique', '4-hours-or-less']   

                                    nutrition  n_steps  \
0       [51.5, 0.0, 13.0, 0.0, 2.0, 0.0, 4.0]       11   
1   [173.4, 18.0, 0.0, 17.0, 22.0, 35.0, 1.0]        9   
2  [269.8, 22.0, 32.0, 48.0, 39.0, 27.0, 5.0]        6   
3   [368.1, 17.0, 10.0, 2.0, 14.0, 8.0, 20.0]       11   
4   [352.9, 1.0, 337.0, 23.0, 3.0, 0.0, 28.0]        5   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

## Food.com Recipes with Search Terms and Tags

In [ ]:
# Create and Display Data
df_labels = pd.read_csv("foodcom-recipes-with-search-terms-and-tags/recipes_w_search_terms.csv")
df_labels.head()

id                                   name  \
0   96313            Grilled Garlic Cheese Grits   
1  232037  Simple Shrimp and Andouille Jambalaya   
2   41090             black-and-white bean salad   
3   60656             Crock Pot Italian Zucchini   
4  232047          Beef Stew With Dried Cherries   

                                                                                                                                                                                                                                                                                                                                                                                                description  \
0                                                                                             We love grits, this is another good way to serve them. A great alternative to a baked potato when served with grilled steak or chicken. I belive this recipe could be made with instant grits.The 2 1/2 hours for refrigeration is not include in time. The recipe comes from Tast of Home's Light and Tasty.   
1                                                                                                                                                                                                                                                                Simple, easy and very tasty for when you are in the mood for jambalaya. My kids loved it! From Cook's Illustrated "Quick Recipe" Cookbook.   
2                                                                                                                                                                                                                                                                                                                                                                                                       NaN   
3                                                                                                                                                                                                                                                                                                                                                 This is a good recipe for weight watchers. It is 0 points   
4  This is a fabulous stew that came from one of the Seattle Junior League cookbooks.  I've tweaked it a bit over the years.  It fills the house with an amazing aroma and tastes as good as it smells.  This takes a while to make, so I often do it on a weekend afternoon and then reheat it later in the week. Although the recipe calls for dried sour cherries, I have also made it with dried bings.   

                                                                                                                                                                                                         ingredients  \
0                                                                                                                                                ['water', 'grits', 'salt', 'cheddar cheese', 'garlic', 'olive oil']   
1  ['onion', 'red bell pepper', 'garlic cloves', 'large shrimp', 'salt', 'hot pepper sauce', 'vegetable oil', 'andouille sausage', 'long grain rice', 'bay leaves', 'diced tomatoes', 'clam juice', 'fresh parsley']   
2                                                           ['white beans', 'canned black beans', 'tomatoes', 'onion', 'celery', 'white wine vinegar', 'italian parsley', 'table salt', 'black pepper', 'olive oil']   
3                                                                           ['zucchini', 'yellow squash', 'diced tomatoes', 'onion', 'garlic', 'green bell pepper', 'italian seasoning', 'water', 'salt and pepper']   
4                          ['beef stew meat', 'flour', 'salt', 'allspice', 'cinnamon', 'black pepper', 'vegetable oil', 'onions', 'dried sour cherries', 'sugar', 'water', 'dry red wine', 'beef stock', 'mushroom']   

  

## Merge Interactions and Recipes

In [ ]:
df_interim = pd.merge(df_interactions, df_recipes, right_on='id', left_on='recipe_id')
df_interim.head()

user_id  recipe_id        date  rating  \
0    38094      40893  2003-02-17       4   
1  1293707      40893  2011-12-21       5   
2     8937      44394  2002-12-01       4   
3   126440      85009  2010-02-27       5   
4    57222      85009  2011-10-01       5   

                                                                                                                                                                                                          review  \
0                                                                     Great with a salad. Cooked on top of stove for 15 minutes.Added a shake of cayenne and a pinch of salt.  Used low fat sour cream.  Thanks.   
1  So simple, so delicious! Great for chilly fall evening. Should have doubled it ;)<br/><br/>Second time around, forgot the remaining cumin. We usually love cumin, but didn't notice the missing 1/2 teaspoon!   
2                                                                                                            This worked very well and is EASY.  I used not quite a whole package (10oz) of white chips.  Great!   
3                                                                                                                                           I made the Mexican topping and took it to bunko.  Everyone loved it.   
4                                                                                                                                      Made the cheddar bacon topping, adding a sprinkling of black pepper. Yum!   

                                   name     id  minutes  contributor_id  \
0  white bean   green chile pepper soup  40893      495            1533   
1  white bean   green chile pepper soup  40893      495            1533   
2      devilicious cookie cake delights  44394       20           56824   
3                 baked potato toppings  85009       10           64342   
4                 baked potato toppings  85009       10           64342   

    submitted  \
0  2002-09-21   
1  2002-09-21   
2  2002-10-27   
3  2004-02-25   
4  2004-02-25   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          tags  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
1                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
2  ['30-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'pre

In [ ]:
df_interim.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1132367 entries, 0 to 1132366
Data columns (total 17 columns):
 #   Column          Non-Null Count    Dtype 
---  ------          --------------    ----- 
 0   user_id         1132367 non-null  int64 
 1   recipe_id       1132367 non-null  int64 
 2   date            1132367 non-null  object
 3   rating          1132367 non-null  int64 
 4   review          1132198 non-null  object
 5   name            1132366 non-null  object
 6   id              1132367 non-null  int64 
 7   minutes         1132367 non-null  int64 
 8   contributor_id  1132367 non-null  int64 
 9   submitted       1132367 non-null  object
 10  tags            1132367 non-null  object
 11  nutrition       1132367 non-null  object
 12  n_steps         1132367 non-null  int64 
 13  steps           1132367 non-null  object
 14  description     1108857 non-null  object
 15  ingredients     1132367 non-null  object
 16  n_ingredients   1132367 non-null  int64 
dtypes: int64

## Final Dataframe - Merge and Cleaning

In [ ]:
df_final = pd.merge(df_interim, df_labels, left_on='id', right_on='id', how='inner', suffixes=('', '_remove'))

# remove the duplicate columns
df_final.drop([i for i in df_final.columns if 'remove' in i],
               axis=1, inplace=True)

df_final.head()

user_id  recipe_id        date  rating  \
0    38094      40893  2003-02-17       4   
1  1293707      40893  2011-12-21       5   
2     8937      44394  2002-12-01       4   
3   126440      85009  2010-02-27       5   
4    57222      85009  2011-10-01       5   

                                                                                                                                                                                                          review  \
0                                                                     Great with a salad. Cooked on top of stove for 15 minutes.Added a shake of cayenne and a pinch of salt.  Used low fat sour cream.  Thanks.   
1  So simple, so delicious! Great for chilly fall evening. Should have doubled it ;)<br/><br/>Second time around, forgot the remaining cumin. We usually love cumin, but didn't notice the missing 1/2 teaspoon!   
2                                                                                                            This worked very well and is EASY.  I used not quite a whole package (10oz) of white chips.  Great!   
3                                                                                                                                           I made the Mexican topping and took it to bunko.  Everyone loved it.   
4                                                                                                                                      Made the cheddar bacon topping, adding a sprinkling of black pepper. Yum!   

                                   name     id  minutes  contributor_id  \
0  white bean   green chile pepper soup  40893      495            1533   
1  white bean   green chile pepper soup  40893      495            1533   
2      devilicious cookie cake delights  44394       20           56824   
3                 baked potato toppings  85009       10           64342   
4                 baked potato toppings  85009       10           64342   

    submitted  \
0  2002-09-21   
1  2002-09-21   
2  2002-10-27   
3  2004-02-25   
4  2004-02-25   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          tags  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
1                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
2  ['30-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'pre

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1093135 entries, 0 to 1093134
Data columns (total 21 columns):
 #   Column               Non-Null Count    Dtype 
---  ------               --------------    ----- 
 0   user_id              1093135 non-null  int64 
 1   recipe_id            1093135 non-null  int64 
 2   date                 1093135 non-null  object
 3   rating               1093135 non-null  int64 
 4   review               1092973 non-null  object
 5   name                 1093134 non-null  object
 6   id                   1093135 non-null  int64 
 7   minutes              1093135 non-null  int64 
 8   contributor_id       1093135 non-null  int64 
 9   submitted            1093135 non-null  object
 10  tags                 1093135 non-null  object
 11  nutrition            1093135 non-null  object
 12  n_steps              1093135 non-null  int64 
 13  steps                1093135 non-null  object
 14  description          1070344 non-null  object
 15  ingredients    

# Pre-Process Data & Split

## Subset Dataset

In [ ]:
df_data = df_final.copy()
df_data.drop(["user_id","submitted","contributor_id","id"], axis=1, inplace=True)
df_data.head()

recipe_id        date  rating  \
0      40893  2003-02-17       4   
1      40893  2011-12-21       5   
2      44394  2002-12-01       4   
3      85009  2010-02-27       5   
4      85009  2011-10-01       5   

                                                                                                                                                                                                          review  \
0                                                                     Great with a salad. Cooked on top of stove for 15 minutes.Added a shake of cayenne and a pinch of salt.  Used low fat sour cream.  Thanks.   
1  So simple, so delicious! Great for chilly fall evening. Should have doubled it ;)<br/><br/>Second time around, forgot the remaining cumin. We usually love cumin, but didn't notice the missing 1/2 teaspoon!   
2                                                                                                            This worked very well and is EASY.  I used not quite a whole package (10oz) of white chips.  Great!   
3                                                                                                                                           I made the Mexican topping and took it to bunko.  Everyone loved it.   
4                                                                                                                                      Made the cheddar bacon topping, adding a sprinkling of black pepper. Yum!   

                                   name  minutes  \
0  white bean   green chile pepper soup      495   
1  white bean   green chile pepper soup      495   
2      devilicious cookie cake delights       20   
3                 baked potato toppings       10   
4                 baked potato toppings       10   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          tags  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
1                                                                                                                                                                                                                                                                                                                                                                                                                                         ['weeknight', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'soups-stews', 'beans', 'vegetables', 'easy', 'crock-pot-slow-cooker', 'dietary', 'equipment']   
2  ['30-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'for-large-groups', '5-ingredients-or-less', 'drop-cookies', 'desserts', 'lunch', 'oven', 'easy', 'potluck', 'fall', 'finger-food', 'heirloom-historical', 'holiday-event', 'kid-friendly', 'picnic', 'spring', 'summer', 'winter', 'cakes', 'cookies-and-brownies', 'easter', '

In [ ]:
df_data = df_data.sample(10000)
df_data.describe()

recipe_id        rating       minutes       n_steps  n_ingredients  \
count   10000.000000  10000.000000  10000.000000  10000.000000   10000.000000   
mean   161427.272600      4.402700    101.203300      9.667700       9.016400   
std    131301.279887      1.284639    781.981316      5.671639       3.685117   
min       131.000000      0.000000      0.000000      1.000000       1.000000   
25%     54075.250000      4.000000     22.000000      6.000000       6.000000   
50%    120526.000000      5.000000     40.000000      9.000000       9.000000   
75%    242900.000000      5.000000     70.000000     12.000000      11.000000   
max    536568.000000      5.000000  43230.000000     70.000000      35.000000   

          servings  
count  10000.00000  
mean       6.52030  
std        7.50372  
min        1.00000  
25%        3.00000  
50%        4.00000  
75%        8.00000  
max      144.00000

# Expanding Nutrition

In [ ]:
df_data[['calories','total fat','sugar','sodium','protein','saturated fat','carbohydrates']] = df_data.nutrition.str.split(",",expand=True)
df_data['calories'] = df_data['calories'].apply(lambda x: x.replace("[" ,""))
df_data['carbohydrates'] = df_data['carbohydrates'].apply(lambda x: x.replace("]" ,""))
df_data[['calories','total fat','sugar','sodium','protein','saturated fat','carbohydrates']] =  df_data[['calories','total fat','sugar','sodium','protein','saturated fat','carbohydrates']].astype(float)
df_data.head()

recipe_id        date  rating  \
579752     126538  2008-07-05       5   
598786     354219  2009-02-23       5   
694598     337411  2010-08-19       4   
618265     285378  2013-07-21       0   
616927      67682  2010-04-02       5   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           review  \
579752                                                                                                                                                                                                                                                                                                                                 Very easy and very yummy - a hit with everyone!  A great use of all that Rhubarb growing in my garden.  We suggest serving it warm with vanilla ice-cream.   
598786                                                                                                        This is one of the best things I have made this month! Totally yummy and good. It's so low fat and calorie too! Very good for you dessert. I made it for breakfast for myself this morning too. I'm going to try it with lemons too, as we really like them here. I'll bet you could make this up on the grill too, just use some tin foil. Made and Reviewed for PRMR - Thanks! :)   
694598  It can't get much easier than this recipe Pat.  I did have to omit the parsnips as they are not in season here and we are too rural for them to ship in I guess.  The only other little change was I subbed apple juice for the brandy.  The meat had a different texture than I'm used to (I don't know if it is the way the vinegar reacts to it) but it was still yummy in the end.  I love being able to cook the veggies with the meat.  Thanks for sharing this in Potluck Tag.  :)   
618265                                                                                                                                                                                                                         I have made this recipe twice,First time half of the cup cake stuck to the paper,second same thing happened.Any ideas what cause this,First time I  used Betty Crocker cake mix ,second time Pillbury cake mix.. It was a big waste,as out to the garage it went..   
616927                                                                                                                                                                                                                                                                                                                                                                                                                       Awesome stuff. I could eat this as my meal....yummy, unique flavors.   

                                name  minutes  \
579752      strawberry rhubarb crisp       50   
598786           baked citrus rounds       10   
694598  old fashioned beef pot roast      165   
618265  strawberry preserve cupcakes       45   
616927           green grape delight       10   

                                                                                                                                                                                                                                                                                                                                tags  \
579752                                                                                                                          ['60-minutes-or-less', 'time-to-make', 'course', 'preparation', 'low-protein', 'healthy', 'cobblers

## Remove Null Values

In [ ]:
df_data.isnull().sum()
df_data.dropna(inplace=True)
df_data.describe()

recipe_id       rating       minutes      n_steps  n_ingredients  \
count    9804.000000  9804.000000   9804.000000  9804.000000    9804.000000   
mean   163944.769482     4.404937    101.888719     9.691044       9.028356   
std    131112.405662     1.284184    789.618573     5.685895       3.694386   
min       133.000000     0.000000      0.000000     1.000000       1.000000   
25%     56969.000000     4.000000     22.000000     6.000000       6.000000   
50%    124214.000000     5.000000     40.000000     9.000000       9.000000   
75%    246587.250000     5.000000     70.000000    12.000000      11.000000   
max    536568.000000     5.000000  43230.000000    70.000000      35.000000   

          servings      calories    total fat        sugar       sodium  \
count  9804.000000   9804.000000  9804.000000  9804.000000  9804.000000   
mean      6.534884    467.575316    35.819359    74.741738    29.898817   
std       7.549470    911.667552    95.833527   223.923700    73.098376   
min       1.000000      0.000000     0.000000     0.000000     0.000000   
25%       3.000000    181.675000     9.000000     9.000000     6.000000   
50%       4.000000    320.400000    21.000000    23.000000    16.000000   
75%       8.000000    520.450000    40.000000    65.000000    35.000000   
max     144.000000  38680.100000  4317.000000  5294.000000  4716.000000   

           protein  saturated fat  carbohydrates  
count  9804.000000    9804.000000    9804.000000  
mean     38.445736      45.275398      14.503570  
std     123.886238     118.392483      26.543417  
min       0.000000       0.000000       0.000000  
25%       7.000000       8.000000       4.000000  
50%      20.000000      24.000000       9.000000  
75%      55.000000      52.000000      16.000000  
max    6540.000000    4960.000000     688.000000

In [ ]:
df_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9804 entries, 579752 to 303093
Data columns (total 24 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   recipe_id            9804 non-null   int64  
 1   date                 9804 non-null   object 
 2   rating               9804 non-null   int64  
 3   review               9804 non-null   object 
 4   name                 9804 non-null   object 
 5   minutes              9804 non-null   int64  
 6   tags                 9804 non-null   object 
 7   nutrition            9804 non-null   object 
 8   n_steps              9804 non-null   int64  
 9   steps                9804 non-null   object 
 10  description          9804 non-null   object 
 11  ingredients          9804 non-null   object 
 12  n_ingredients        9804 non-null   int64  
 13  ingredients_raw_str  9804 non-null   object 
 14  serving_size         9804 non-null   object 
 15  servings             9804 non-n

## Text Preprocessing

In [ ]:
df_recommend = df_data[['recipe_id', 'rating', 'name', 'tags', 'description', 'ingredients', 'servings']]

In [ ]:
df_recommend.duplicated().sum()
df_recommend.drop_duplicates(inplace=True)
df_recommend.reset_index(drop=True,inplace=True)
df_recommend.head()

recipe_id  rating                          name  \
0     126538       5      strawberry rhubarb crisp   
1     354219       5           baked citrus rounds   
2     337411       4  old fashioned beef pot roast   
3     285378       0  strawberry preserve cupcakes   
4      67682       5           green grape delight   

                                                                                                                                                                                                                                                                                                                           tags  \
0                                                                                                                          ['60-minutes-or-less', 'time-to-make', 'course', 'preparation', 'low-protein', 'healthy', 'cobblers-and-crisps', 'desserts', 'easy', 'dietary', 'low-sodium', 'low-in-something', '3-steps-or-less']   
1  ['15-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'low-protein', 'healthy', '5-ingredients-or-less', 'side-dishes', 'fruit', 'easy', 'beginner-cook', 'low-fat', 'dietary', 'low-sodium', 'low-cholesterol', 'low-saturated-fat', 'low-calorie', 'healthy-2', 'low-in-something', 'citrus']   
2                                                                                                                                          ['time-to-make', 'course', 'main-ingredient', 'cuisine', 'preparation', 'south-west-pacific', 'main-dish', 'beef', 'australian', 'dietary', 'meat', 'roast-beef', '4-hours-or-less']   
3                                                                                                                                                               ['60-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'cupcakes', 'desserts', 'fruit', 'easy', 'cakes', 'berries', 'strawberries']   
4                                                  ['15-minutes-or-less', 'time-to-make', 'course', 'main-ingredient', 'preparation', 'occasion', 'appetizers', 'lunch', 'salads', 'fruit', 'refrigerator', 'dinner-party', 'spreads', 'dietary', 'low-sodium', 'low-in-something', 'berries', 'grapes', 'brunch', 'equipment']   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  description  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             wonderful treat   
1  i got this recipe several years ago from a cookbook called the treasury of favorite brand name recipes.  we have it often as a side dish when i serve our favorite spicy caribbean dish, because the succulent citrus rounds nicley complement the savory spice blends featured in that caribbean dish.  i think it would also be great with other spicy cuisines as well....perhaps as a side dish to accompany a zesty italian dish or a spicy mexican entree.  it's very simple to prepare, and it uses only 4 common ingredients.  i hope you like it.   
2                                                                                                       

In [ ]:
df_recommend.describe()

recipe_id       rating     servings
count    8841.000000  8841.000000  8841.000000
mean   171708.553105     4.352901     6.431852
std    132286.489234     1.327185     7.195109
min       133.000000     0.000000     1.000000
25%     61856.000000     4.000000     3.000000
50%    135773.000000     5.000000     4.000000
75%    259993.000000     5.000000     8.000000
max    536568.000000     5.000000   144.000000

In [ ]:
import string

def list_conversion(data):
    translate_table = str.maketrans('', '', string.punctuation + "-[]")
    return data.translate(translate_table)

columns = ['tags', 'ingredients', 'description']
df_recommend[columns] = df_recommend[columns].applymap(list_conversion)
df_recommend["recommend"] = df_recommend["tags"] + df_recommend["description"] + df_recommend["ingredients"]
df_recommend = df_recommend[~df_recommend.duplicated("name")]
df_recommend.reset_index(drop=True,inplace=True)
df_recommend.head()

recipe_id  rating                          name  \
0     126538       5      strawberry rhubarb crisp   
1     354219       5           baked citrus rounds   
2     337411       4  old fashioned beef pot roast   
3     285378       0  strawberry preserve cupcakes   
4      67682       5           green grape delight   

                                                                                                                                                                                                                                      tags  \
0                                                                                           60minutesorless timetomake course preparation lowprotein healthy cobblersandcrisps desserts easy dietary lowsodium lowinsomething 3stepsorless   
1  15minutesorless timetomake course mainingredient preparation lowprotein healthy 5ingredientsorless sidedishes fruit easy beginnercook lowfat dietary lowsodium lowcholesterol lowsaturatedfat lowcalorie healthy2 lowinsomething citrus   
2                                                                                                       timetomake course mainingredient cuisine preparation southwestpacific maindish beef australian dietary meat roastbeef 4hoursorless   
3                                                                                                                     60minutesorless timetomake course mainingredient preparation cupcakes desserts fruit easy cakes berries strawberries   
4                                    15minutesorless timetomake course mainingredient preparation occasion appetizers lunch salads fruit refrigerator dinnerparty spreads dietary lowsodium lowinsomething berries grapes brunch equipment   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      description  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 wonderful treat   
1  i got this recipe several years ago from a cookbook called the treasury of favorite brand name recipes  we have it often as a side dish when i serve our favorite spicy caribbean dish because the succulent citrus rounds nicley complement the savory spice blends featured in that caribbean dish  i think it would also be great with other spicy cuisines as wellperhaps as a side dish to accompany a zesty italian dish or a spicy mexican entree  its very simple to prepare and it uses only 4 common ingredients  i hope you like it   
2                                                                                                                                                                                                                                                                                                                     from our local paper  in the original recipe 3 brown onions roughly chopped were used but due to allergy issues they have been omitted and also 2 bunches of baby carrots trimmed and 3 parsnips and  i have added potatoes   
3                                                                                                                    

## TF-IDF (Term Frequency-Inverse Document Frequency)

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import StandardScaler
from sklearn.metrics.pairwise import cosine_similarity, linear_kernel
from scipy.sparse import hstack

tf = TfidfVectorizer(ngram_range=(1, 2), min_df=2)

# Initialize Recommendations and Name
rec_tfidf = tf.fit_transform(df_recommend["recommend"])
name_tfidf = tf.fit_transform(df_recommend['name'])

rec_sim = cosine_similarity(rec_tfidf, rec_tfidf)
name_sim = cosine_similarity(name_tfidf, name_tfidf)

rec_sim_df = pd.DataFrame(rec_sim)
name_sim_df = pd.DataFrame(name_sim)


# Create matrices with Recommendation and Name & Serving sizes
# Standardize the 'servings' column
scaler = StandardScaler()
df_recommend['servings_standardized'] = scaler.fit_transform(df_recommend['servings'].values.reshape(-1, 1))

combined_features = hstack([df_recommend['servings_standardized'].values.reshape(-1, 1), name_tfidf])

# Cosine similarity for combined features
combined_sim_matrix = cosine_similarity(combined_features, combined_features)

# Create a DataFrame from the matrix
combined_sim_df = pd.DataFrame(combined_sim_matrix, columns=df_recommend.index, index=df_recommend.index)


combined_sim_df.head()

0         1         2         3         4         5         6     \
0  1.000000 -0.142608 -0.025210 -0.111346 -0.142608  0.097522 -0.025210   
1 -0.142608  1.000000  0.017872  0.191413  0.101095 -0.069134  0.017872   
2 -0.025210  0.017872  1.000000  0.033838  0.017872 -0.012222  0.003159   
3 -0.111346  0.191413  0.033838  1.000000  0.191413 -0.130898  0.033838   
4 -0.142608  0.101095  0.017872  0.191413  1.000000 -0.069134  0.141695   

       7         8         9         10        11        12        13    \
0 -0.142608  0.097522 -0.142608  0.276046  0.359360  0.415385 -0.142608   
1  0.101095 -0.069134  0.101095 -0.195690 -0.254751 -0.294467  0.101095   
2  0.017872 -0.012222  0.017872 -0.034594 -0.045035 -0.052056  0.017872   
3  0.191413 -0.130898  0.191413 -0.370519 -0.482347 -0.557544  0.191413   
4  0.101095 -0.069134  0.101095 -0.195690 -0.254751 -0.294467  0.101095   

       14        15        16        17        18        19        20    \
0 -0.025210 -0.025210 -0.142608  0.381533 -0.270014  0.396770 -0.025210   
1  0.017872  0.017872  0.101095 -0.270469  0.191413 -0.281271  0.017872   
2  0.003159  0.003159  0.017872 -0.047814  0.033838 -0.049723  0.003159   
3  0.033838  0.033838  0.191413 -0.512107  0.362423 -0.532559  0.033838   
4  0.017872  0.017872  0.101095 -0.270469  0.191413 -0.281271  0.017872   

       21        22        23        24        25        26        27    \
0 -0.025210 -0.270014  0.381533  0.359360 -0.142608 -0.142608 -0.142608   
1  0.017872  0.191413 -0.270469 -0.254751  0.101095  0.101095  0.101095   
2  0.003159  0.033838 -0.047814 -0.011089  0.017872  0.017872  0.017872   
3  0.033838  0.362423 -0.512107 -0.482347  0.191413  0.191413  0.191413   
4  0.017872  0.191413 -0.270469 -0.254751  0.101095  0.101095  0.101095   

       28        29        30        31        32        33        34    \
0  0.276046 -0.142608 -0.142608 -0.142608 -0.270014  0.097522 -0.142608   
1 -0.195690  0.101095  0.101095  0.101095  0.191413 -0.069134  0.101095   
2 -0.034594  0.017872  0.093156  0.017872  0.033838 -0.012222  0.017872   
3 -0.370519  0.191413  0.191413  0.191413  0.362423 -0.130898  0.191413   
4 -0.195690  0.101095  0.101095  0.101095  0.191413 -0.069134  0.101095   

       35        36        37        38        39        40        41    \
0  0.276046 -0.142608 -0.142608 -0.142608 -0.086195 -0.142608  0.448517   
1 -0.195690  0.101095  0.101095  0.101095  0.061104  0.101095 -0.317954   
2 -0.034594  0.017872  0.017872  0.017872  0.010802  0.017872 -0.056208   
3 -0.370519  0.191413  0.191413  0.191413  0.115694  0.191413 -0.602015   
4 -0.195690  0.101095  0.101095  0.101095  0.061104  0.101095 -0.317954   

       42        43        44        45        46        47        48    \
0  0.201167 -0.025210 -0.142608 -0.270014 -0.270014  0.415385 -0.142608   
1 -0.142608  0.017872  0.250676  0.191413  0.191413 -0.294467  0.101095   
2 -0.025210  0.003159  0.017872  0.033838  0.033838 -0.052056  0.017872   
3 -0.270014  0.033838  0.191413  0.362423  0.362423 -0.557544  0.191413   
4 -0.142608  0.017872  0.101095  0.191413  0.191413 -0.294467  0.101095   

       49        50        51        52        53        54        55    \
0 -0.192402 -0.270014  0.000528 -0.234798  0.097522 -0.142608 -0.025210   
1  0.136394  0.191413  0.101095  0.166449 -0.069134  0.101095  0.017872   
2  0.024112  0.033838  0.017872  0.029425 -0.012222  0.017872  0.003159   
3  0.258249  0.362423  0.436746  0.315155 -0.130898  0.191413  0.033838   
4  0.136394  0.191413  0.101095  0.166449 -0.069134  0.101095  0.017872   

       56        57        58        59        60        61        62    \
0 -0.142608 -0.270014  0.443906  0.097522 -0.142608 -0.270014  0.276046   
1  0.101095  0.191413 -0.314686 -0.069134  0.101095  0.191413 -0.195690   
2  0.017872  0.033838 -0.055630 -0.012222  0.017872  0.033838 -0.034594   
3  0.191413  0.362423 -0.595827 -0.130898  0.191413  0.362423 -0.370519   
4  0.101095  0.191413 -0

In [ ]:
name_sim_df.head()

0     1     2         3     4     5         6     7     8     9     \
0  1.000000   0.0   0.0  0.222329   0.0   0.0  0.000000   0.0   0.0   0.0   
1  0.000000   1.0   0.0  0.000000   0.0   0.0  0.000000   0.0   0.0   0.0   
2  0.000000   0.0   1.0  0.000000   0.0   0.0  0.000000   0.0   0.0   0.0   
3  0.222329   0.0   0.0  1.000000   0.0   0.0  0.000000   0.0   0.0   0.0   
4  0.000000   0.0   0.0  0.000000   1.0   0.0  0.130807   0.0   0.0   0.0   

   10    11    12    13    14    15    16    17    18    19    20    21    \
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

   22    23        24    25    26    27    28    29        30    31    32    \
0   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
1   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
2   0.0   0.0  0.056821   0.0   0.0   0.0   0.0   0.0  0.079531   0.0   0.0   
3   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
4   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   

   33    34    35    36    37    38    39    40    41    42    43        44    \
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.166404   
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   

   45    46    47    48    49    50        51    52    53    54    55    56    \
0   0.0   0.0   0.0   0.0   0.0   0.0  0.168913   0.0   0.0   0.0   0.0   0.0   
1   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0   
2   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0   
3   0.0   0.0   0.0   0.0   0.0   0.0  0.324065   0.0   0.0   0.0   0.0   0.0   
4   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   0.0   0.0   0.0   

   57    58    59    60    61    62    63    64    65        66    67    68    \
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.053508   0.0   0.0   
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   0.0   

       69    70    71    72    73    74    75    76    77    78    79    80    \
0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1  0.076136   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

   81    82    83    84    85    86    87    88    89    90        91    92    \
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   
1   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   
2   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.070444   0.0   
3   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   
4   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.000000   0.0   

   93    94    95    96    97    98    99    100   101   102   103   104   \
0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1   0.0   0.0   0

# Recommendation System

## Method 1 - Single Factor Recommendation

In [ ]:
recipe_list = df_recommend['servings'].values
recipe_list, recipe_list.shape

(array([10,  4,  6, ...,  4,  4, 16]), (8397,))

In [ ]:
recipe_idx = np.where(recipe_list == 2)[0][0]
recipe_idx

52

In [ ]:
initial_input = df_recommend.loc[recipe_idx, 'name']
initial_input

'gabriels sauteed fava beans'

In [ ]:
recipe_similarities = combined_sim_df.iloc[recipe_idx].values
recipe_similarities

array([-0.23479829,  0.16644898,  0.02942499, ...,  0.16644898,
        0.16644898, -0.41943825])

In [ ]:
similar_recipe_idxs = np.argsort(-recipe_similarities)[1:6]
similar_recipes = df_recommend.loc[similar_recipe_idxs, 'name'].values
similar_recipes

array(['fava beans supreme', 'fava beans just like grandma made',
       'caipirissima', 'bulgoki', 'cognac highball'], dtype=object)

## Method 2 - Multi-Factor Recommendation

In [ ]:
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
from sklearn.base import BaseEstimator, TransformerMixin
from scipy.sparse import hstack
import scipy.sparse as sp
import pandas as pd
import numpy as np

In [ ]:
def get_user_input_recommendations(user_input, pipeline, df_recommend, top_n=5):
    # Create a DataFrame with the user input
    user_df = pd.DataFrame([user_input], columns=['user_input'])

    # Transform the user input using the pipeline
    transformed_input = pipeline.transform(user_df)

    # Calculate similarities between the user input and existing recipes
    user_similarities = linear_kernel(transformed_input.values.reshape(1, -1), pipeline.named_steps['recipe_model'].transform(df_recommend))

    # Get the indices of the top N similar recipes
    similar_recipe_idxs = np.argsort(-user_similarities[0])[0:top_n]

    # Retrieve the names of the recommended recipes
    recommended_recipes = df_recommend.loc[similar_recipe_idxs, 'name'].values

    return recommended_recipes

In [ ]:
class TextFeatures(BaseEstimator, TransformerMixin):
    def __init__(self, column):
        self.column = column
        self.vectorizer = TfidfVectorizer(ngram_range=(1, 2), min_df=2)

    def fit(self, X, y=None):
        if self.column in X.columns:
            self.vectorizer.fit(X[self.column])
        return self

    def transform(self, X):
        if self.column in X.columns:
            return self.vectorizer.transform(X[self.column])
        else:
            return sp.csr_matrix((X.shape[0], 1))  # Return a sparse matrix if the column is not present


class NumericalFeatures(BaseEstimator, TransformerMixin):
    def fit(self, X, y=None):
        return self

    def transform(self, X):
        scaler = StandardScaler()
        return scaler.fit_transform(X[['rating', 'servings']])

class RecipeRecommendationModel(BaseEstimator, TransformerMixin):
    def fit(self, X, y=None):
        return self

    def transform(self, X):
        all_features = hstack([X[0], X[1], X[2]])
        recipe_similarities = linear_kernel(all_features, all_features)
        return pd.DataFrame(recipe_similarities, columns=df_recommend.index, index=df_recommend.index)

# Create a pipeline
text_pipeline = Pipeline([
    ('text_ingredients', TextFeatures(column='ingredients'))
])

numerical_pipeline = Pipeline([
    ('numerical_features', NumericalFeatures())
])

full_pipeline = Pipeline([
    ('feature_union', FeatureUnion([
        ('text_pipeline', text_pipeline),
        ('numerical_pipeline', numerical_pipeline)
    ])),
    ('recipe_model', RecipeRecommendationModel())
])

In [ ]:
# Example usage
user_input = {
    'ingredients': 'chicken, rice, tomatoes',
    'servings': 4,
    'rating':5
}

# Transform user input using the pipeline and get recommendations
user_recommendations = get_user_input_recommendations(user_input, full_pipeline, df_recommend)

print("User Input:")
print(user_input)
print("\nRecommendations:")
print(user_recommendations)